In [286]:
from functools import reduce

def nest(f,n,x):
    return reduce(lambda a,b:f(a),range(n),x)

def fixedpoint(f,x):
    found=False
    while not(found):
        y=f(x)
        if y==x:
            found=True
        else:
            x=y
    return x

In [230]:
#versão1

from math import sqrt

def dist(p,q):
    return sqrt((p[0]-q[0])**2+(p[1]-q[1])**2)

#a

def dif(topbot):
    return topbot[0]-topbot[1]

def difmaxmin(w):
    def onebyone(topbot,x):
        if x>topbot[0]:
            return (x,topbot[1])
        elif x<topbot[1]:
            return (topbot[0],x)
        else:
            return topbot
       
    return dif(reduce(onebyone,w[1:],(w[0],w[0])))

#b

def pathlen(points):
    return reduce(lambda x,y:x+y,map(dist,points[:-1],points[1:]),0)

def pathof(i,base,requests,allocs):
    return [base[i]]+[requests[j] for j in range(len(requests)) if allocs[j]==i]

def cost(base,requests,allocs):
    return difmaxmin([pathlen(pathof(i,base,requests,allocs)) for i in range(len(base))])

#c

def anybetter(base,wrequests,wallocs,thecost):
    return any([cost(base,req,alc)<thecost for req in wrequests for alc in wallocs])


In [246]:
#versão2

def dist(p,q):
    return abs(p-q)

#a

def pathof(i,base,requests,allocs):
    return [base[i]]+[requests[j] for j in range(len(requests)) if allocs[j]==i]

def sumlist(w):
    return reduce(lambda x,y:x+y,w,0)

def pathlen(points):
    return sumlist(map(dist,points[:-1],points[1:]))

#b

def calcdist(base,requests,allocs):
    return sumlist([pathlen(pathof(i,base,requests,allocs)) for i in range(len(base))])

#c   

def posmin(m):
    def newmin(pos,new):
        if m[new[0]][new[1]]<m[pos[0]][pos[1]]:
            return new
        else:
            return pos
    
    return reduce(newmin,[(i,j) for i in range(len(m)) for j in range(len(m[0]))],(0,0))

def bestcomb(n,wrequests,wallocs):
    return posmin([[calcdist([0]*n,req,alc) for alc in wallocs] for req in wrequests])

In [253]:
#versão3


def penal(assign):
    return reduce(lambda x,y:x+y,[assign[i][1] for i in range(len(assign)) if assign[i][0]<i],0)

#b

def melhor(assigns):
    def step(best,new):
        if penal(assigns[new])<penal(best):
            return assigns[new]
        else:
            return best
    
    return reduce(step,range(1,len(assigns)),assigns[0])
    
#c 

def recalendar(assign,i):
    def puti(passign,j):
        return passign[:j]+[assign[i]]+passign[j:]
    return [puti(assign[:i]+assign[i+1:],j) for j in range(len(assign)) if j!=i]


def recalpos(assign,i):
    return penal(melhor(recalendar(assign,i)))<penal(assign)

In [260]:
#versão4

#a

def nfalhas(assign):
    return len([i for i in range(len(assign)) if assign[i]<i])

#b

def escolhe(asg1,asg2):
    if nfalhas(asg1)<nfalhas(asg2):
        return asg1
    else:
        return asg2
    
def menosfalhas(assigns):
    return reduce(escolhe,assigns[1:],assigns[0]) 

#c

def antecip(assign,i):
    def puti(passign,j):
        return passign[:j]+[assign[i]]+passign[j:]
    return [puti(assign[:i]+assign[i+1:],j) for j in range(i)]

def antpos(assign,i):
    return menosfalhas([assign]+antecip(assign,i))

In [266]:
#versão5

#a

def where(w,x):
    return [i for i in range(len(w)) if w[i]==x][0]

def custo(w,acc):
    def each(c,x):
        return c+where(w,x)
    
    return reduce(each,acc,0)

#b

def highest(vals):
    return reduce(thebest,vals[1:],vals[0])

def thebest(t,r):
    if r[-1]>t[-1]:
        return r
    else:
        return t

def maisvisitada(w,acc):
    return highest([(i,len([x for x in acc if x==w[i]])) for i in range(len(w))])[0]
    
#c

def melhorcomb(wlist,wacc):
    return highest([((i,j),-custo(wlist[i],wacc[j])) for i in range(len(wlist)) for j in range(len(wacc))])[0]

In [273]:
#versão6

#a

def custotal(costs):
    return reduce(lambda x,y:x+y,costs,0)
    
#b

def minval(w):
    return reduce(lambda x,y: y if y<x else x,w[1:],w[0])

def melhores(wlist):
    def which(x):
        return ([costs for costs in wlist if custotal(costs)==x],x)
        
    return which(minval([custotal(costs) for costs in wlist]))

#c

def troca(w,i,j):
    def iporj(x):
        if x==i:
            return j
        elif x==j:
            return i
        else:
            return x
    return list(map(iporj,w))

def melhoresportroca(costs,n):
    return melhores([troca(costs,i,j) for i in range(n+1) for j in range(i)])[0]

In [284]:
#versão7

#a

def invs(w):
    def lenfirst(ww):
        if len(ww)==0:
            return (0,len(w))
        else:
            return (len(ww),ww[0])
    
    return lenfirst([i for i in range(1,len(w)) if w[i]<w[i-1]])

#b


def melhorord(ws):
    def bestof(poss):
        def update(best,new):
            if new[1][0]<best[1][0] or (new[1][0]==best[1][0] and new[1][1]>best[1][1]):
                return new
            else:
                return best
        
        return reduce(update,poss[1:],poss[0])
    
    return bestof([(i,invs(ws[i])) for i in range(len(ws))])[0]

#c

def todastrocas(w):
    return [w[:i]+[w[j]]+w[i+1:j]+[w[i]]+w[j+1:] for i in range(len(w)) for j in range(i+1,len(w))]

def valetrocar(w):
    return melhorord([w]+todastrocas(w))!=0

In [296]:
#versão8

#a

def segs(w):
    def onebyone(r,i):
        if i==0 or w[i-1]<=w[i]:
            return r[:-1]+[r[-1]+[w[i]]]
        else:
            return r+[[w[i]]]
    
    return reduce(onebyone,range(len(w)),[[]])

def junta(segs):
    return reduce(lambda x,y:x+y,segs,[])

#b

def maxval(u):
    def update(x,y):
        if y>x:
            return y
        else:
            return x
    
    return reduce(update,u[1:],u[0])

def taxa(w):
    return maxval(list(map(len,segs(w))))/len(w)

#c

def bestof(ws):
    return maxval([taxa(w) for w in ws])